In [1]:
import networkx as nx
from node2vec import Node2Vec
from node2vec.edges import HadamardEmbedder
import gensim
import pandas as pd
import matplotlib as plt
import csv
import regex as re
import pickle
import random
import time
import numpy as np
from numpy import argmax
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import Input, Sequential, load_model
from keras.layers import Conv2D, MaxPooling2D
from keras.layers import Dense, Activation, Flatten, Dropout
from keras.layers import Embedding, LSTM
from keras.layers.merge import concatenate
from keras.callbacks import EarlyStopping
from keras import utils, optimizers, Model
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import roc_auc_score, average_precision_score

Using TensorFlow backend.


In [2]:
from itertools import islice

def take(n, iterable):
    "Return first n items of the iterable as a list"
    return list(islice(iterable, n))

In [3]:
gensim.__version__

'3.7.2'

In [4]:
!ls ./FromTermProject

CHN_data_df_v4.csv		   company_SEA_2010-2014_cosine_sim.csv
SEA_data_df_v4.csv		   investments_final_SEA_2010-2014.csv
companies_final_SEA_2010-2014.csv  investor_SEA_2010-2014_cosine_sim.csv


# Reading in Data Files

In [5]:
SEA_data_df_all = pd.read_csv("FromTermProject/SEA_data_df_v4.csv")
SEA_data_df = SEA_data_df_all[SEA_data_df_all["label"]==1]

In [6]:
SEA_data_df_all.head()

from                      to company_origin company_category_grp  \
0  500-startups              2359-media            SGP               Mobile   
1  500-startups  milaap-social-ventures            SGP   Financial Services   
2  500-startups                grabtaxi            SGP   Travel and Tourism   
3  500-startups              flocations            SGP   Data and Analytics   
4  500-startups                    ag-p            PHL               Others   

   company_funding_to_date investor_type  investor_funding_to_date  label  \
0                 615000.0  organization                14800000.0      0   
1                5825000.0  organization                14800000.0      0   
2              620000000.0  organization                14800000.0      0   
3                1823500.0  organization                14800000.0      0   
4              106000000.0  organization                14800000.0      0   

   company_comm_id  investor_comm_id  ...  company_betweenness  \
0                5                 2  ...                  0.0   
1                5                 2  ...                229.0   
2                0                 2  ...                826.0   
3               15                 2  ...                369.0   
4                0                 2  ...                  0.0   

   investor_betweenness  company_closeness  investor_closeness  \
0                6524.0           0.000034            0.000012   
1                6524.0           0.000034            0.000012   
2                6524.0           0.000032            0.000012   
3                6524.0           0.000034            0.000012   
4                6524.0           0.000015            0.000012   

   company_cluster_coef  investor_cluster_coef  company_page_rank  \
0              1.000000               0.152709           0.005749   
1              0.552381               0.152709           0.006769   
2              0.190476               0.152709           0.006716   
3              0.329710               0.152709           0.008632   
4              0.000000               0.152709           0.000809   

   investor_page_rank  company_eccentricity  investor_eccentricity  
0            0.005112                     6                      6  
1            0.005112                     5                      6  
2            0.005112                     6                      6  
3            0.005112                     6                      6  
4            0.005112                     0                      6  

[5 rows x 22 columns]

In [7]:
CHN_data_df_all = pd.read_csv("FromTermProject/CHN_data_df_v4.csv")
CHN_data_df = CHN_data_df_all[CHN_data_df_all["label"]==1]

In [8]:
CHN_data_df_all.head()

from           to company_origin     company_category_grp  \
0  36kr_i   shijiebang        Beijing                Education   
1  36kr_i        inman      Guangzhou    Commerce and Shopping   
2  36kr_i     58-com_s    CHN - Other                   Others   
3  36kr_i    six-waves   Causeway Bay                   Others   
4  36kr_i  kaikeba-com        Beijing  Media and Entertainment   

   company_funding_to_date investor_type  investor_funding_to_date  label  \
0               32000000.0  organization                 5000000.0      0   
1               20000000.0  organization                 5000000.0      0   
2              145000000.0  organization                 5000000.0      0   
3               87677856.0  organization                 5000000.0      0   
4               41647446.0  organization                 5000000.0      0   

   company_comm_id  investor_comm_id  ...  company_betweenness  \
0                0                 0  ...             0.000000   
1               28                 0  ...          1846.583333   
2                1                 0  ...             0.000000   
3                0                 0  ...             0.000000   
4                0                 0  ...           586.000000   

   investor_betweenness  company_closeness  investor_closeness  \
0                   0.0           0.000011            0.000005   
1                   0.0           0.000013            0.000005   
2                   0.0           0.000013            0.000005   
3                   0.0           0.000002            0.000005   
4                   0.0           0.000013            0.000005   

   company_cluster_coef  investor_cluster_coef  company_page_rank  \
0              1.000000                    0.0           0.000308   
1              0.763889                    0.0           0.002535   
2              0.456324                    0.0           0.001163   
3              0.000000                    0.0           0.000241   
4              0.666667                    0.0           0.001390   

   investor_page_rank  company_eccentricity  investor_eccentricity  
0            0.000382                     7                      0  
1            0.000382                     5                      0  
2            0.000382                     6                      0  
3            0.000382                     0                      0  
4            0.000382                     7                      0  

[5 rows x 22 columns]

In [9]:
SEA_data_graph = nx.Graph()
SEA_data_graph.add_nodes_from(SEA_data_df['from'].tolist(), bipartite=0)
SEA_data_graph.add_nodes_from(SEA_data_df['to'].tolist(), bipartite=1)
SEA_data_graph.add_edges_from(
    [(row['from'], row['to']) for idx, row in SEA_data_df.iterrows()])

In [10]:
CHN_data_graph = nx.Graph()
CHN_data_graph.add_nodes_from(CHN_data_df['from'].tolist(), bipartite=0)
CHN_data_graph.add_nodes_from(CHN_data_df['to'].tolist(), bipartite=1)
CHN_data_graph.add_edges_from(
    [(row['from'], row['to']) for idx, row in CHN_data_df.iterrows()])

In [11]:
print(SEA_data_graph.edges(data=True))

[('500-startups', '99-co', {}), ('500-startups', 'carousell', {}), ('500-startups', 'imoney-group', {}), ('500-startups', 'yogatrail', {}), ('500-startups', 'playbasis', {}), ('500-startups', 'qraved', {}), ('500-startups', 'pomelo', {}), ('500-startups', 'catchthatbus', {}), ('500-startups', 'smove', {}), ('500-startups', 'trustedcompany-com', {}), ('500-startups', 'cargobase', {}), ('500-startups', 'omise-co-ltd', {}), ('500-startups', 'tappy-pte--ltd-', {}), ('8capita-partners', 'collabspot', {}), ('8capita-partners', 'e27', {}), ('8capita-partners', 'hipflat', {}), ('a-soriano-corporation', 'ag-p', {}), ('accel-partners', 'mig-me', {}), ('accel-x-pte-ltd', 'infindo-technology-sdn-bhd', {}), ('accel-x-pte-ltd', 'inverted-edge', {}), ('access-industries', 'lazada-group_s', {}), ('access-industries', 'zalora_s', {}), ('ace-singapore', 'viddsee', {}), ('adrian-vanzyl', 'playbasis', {}), ('aif-capital', 'huy-vietnam', {}), ('alacrity-capital', 'glints', {}), ('alibaba_i', 'singapore-pos

In [12]:
pos = {node:[0, i] for i,node in enumerate(SEA_data_df['from'])}
pos.update({node:[1, i] for i,node in enumerate(SEA_data_df['to'])})
nx.draw(SEA_data_graph, pos, with_labels=False)
# for p in pos:  # raise text positions
#     pos[p][1] += 0.25
# nx.draw_networkx_labels(SEA_data_graph, pos)

/home/w/weeliyen/miniconda3/envs/tsf_gpu_2/lib/python3.6/site-packages/networkx/drawing/nx_pylab.py:611: MatplotlibDeprecationWarning: isinstance(..., numbers.Number)
  if cb.is_numlike(alpha):


# SEA

## Create Embedding Files

In [13]:
SEA_NODE_EMBEDDING_FILENAME = "SEA_graph_node.emb"
SEA_EMBEDDING_MODEL_FILENAME = "SEA_graph_model.model"
SEA_EDGE_EMBEDDING_FILENAME= "SEA_graph_edge.emb"

In [14]:
# Precompute probabilities and generate walks - **ON WINDOWS ONLY WORKS WITH workers=1**
node2vec = Node2Vec(SEA_data_graph, dimensions=64, walk_length=30, num_walks=200, workers=4)  # Use temp_folder for big graphs

# Embed nodes
model = node2vec.fit(window=10, min_count=1, batch_words=4)  # Any keywords acceptable by gensim.Word2Vec can be passed, `diemnsions` and `workers` are automatically passed (from the Node2Vec constructor)

# Save embeddings for later use
model.wv.save_word2vec_format(SEA_NODE_EMBEDDING_FILENAME)

# Save model for later use|
model.save(SEA_EMBEDDING_MODEL_FILENAME)

edges_embs = HadamardEmbedder(keyed_vectors=model.wv)

Computing transition probabilities: 100%|██████████| 682/682 [00:00<00:00, 12455.11it/s]


In [15]:
# Look for most similar nodes
print(model.wv.most_similar('thoughtbuzz'))  # Output node names are always strings

# Look for embeddings on the fly - here we pass normal tuples
edges_embs[('azione-capital-pte-ltd', 'designhub')]

[('graymatics', 0.6579338908195496), ('gnosis-analytics', 0.6566205024719238), ('sprooki', 0.6395983099937439), ('double-helix-tracking-technologies', 0.6322077512741089), ('inverted-edge', 0.624418318271637), ('art-of-click', 0.6206813454627991), ('gimmie', 0.5700980424880981), ('snyppit', 0.5578256249427795), ('digital-news-asia', 0.553549587726593), ('plug-and-play-ventures', 0.5362640619277954)]


array([-7.63419688e-01,  9.19809639e-01,  2.51509249e-02,  1.09815575e-01,
       -2.17968011e+00,  8.20297690e-04,  5.65438494e-02,  3.78109545e-01,
        1.55695258e-02, -2.73341686e-01,  3.01948977e+00, -1.64237416e+00,
        8.97768810e-02,  3.57958376e-01, -1.68946922e-01, -3.43960941e-01,
        3.40772033e-01,  1.74548793e+00,  1.35302389e+00,  1.70494819e+00,
        5.29873595e-02, -3.91761214e-01, -3.34733687e-02, -8.85825396e-01,
       -3.62569443e-03,  2.30375695e+00, -3.60776126e-01, -5.46686113e-01,
        2.03578085e-01,  2.95177661e-03,  1.55858850e+00, -1.04216361e+00,
        8.84600431e-02,  5.22284448e-01, -6.52549267e-01,  8.45416784e-01,
       -4.11428571e-01,  3.52943867e-01,  3.43006313e-01, -6.50895238e-02,
       -2.33940572e-01,  1.88836694e+00,  7.42332840e+00,  5.27740717e-01,
       -6.77261889e-01,  1.29355466e+00,  1.45504817e-01, -8.01256597e-02,
        4.32672679e-01,  4.21068311e-01, -3.44460934e-01,  2.43399596e+00,
        1.91866338e+00,  

In [16]:
# Get all edges in a separate KeyedVectors instance - use with caution could be huge for big networks
edges_kv = edges_embs.as_keyed_vectors()

# Save embeddings for later use
edges_kv.save_word2vec_format(SEA_EDGE_EMBEDDING_FILENAME)

Generating edge features: 100%|██████████| 232903/232903.0 [00:01<00:00, 160239.40it/s]


In [17]:
# Look for most similar edges - this time tuples must be sorted and as str
edges_kv.most_similar(str(('azione-capital-pte-ltd', 'designhub')))

[("('azione-capital-pte-ltd', 'coupmon')", 0.9987820386886597),
 ("('designhub', 'nicholas-chan')", 0.9985862374305725),
 ("('azione-capital-pte-ltd', 'hundredapples')", 0.9984438419342041),
 ("('azione-capital-pte-ltd', 'dynamic-social-network-analysis')",
  0.9981026649475098),
 ("('azione-capital-pte-ltd', 'clan-fight')", 0.9981023073196411),
 ("('azione-capital-pte-ltd', 'spendcrowd')", 0.9978218078613281),
 ("('hundredapples', 'nicholas-chan')", 0.997676432132721),
 ("('coupmon', 'nicholas-chan')", 0.9971821904182434),
 ("('azione-capital-pte-ltd', 'dealping')", 0.9969444274902344),
 ("('nicholas-chan', 'spendcrowd')", 0.9968436360359192)]

## Reading in Embedding Files

In [18]:
node_params = []
node_params_dict = {}
with open(SEA_NODE_EMBEDDING_FILENAME, "r") as emb_file:
    next(emb_file)
    reader = csv.reader(emb_file, delimiter=" ")
    for row in reader:
        node_name = row[0]
        node_params.append({
            "name": node_name,
            "embedding": [float(item) for item in row[1:]]
        })
        node_params_dict[node_name] = [float(item) for item in row[1:]]
# node_params
node_params_dict

{'gocoin': [2.1852767,
  0.95958894,
  1.7577295,
  -0.52477944,
  0.4141418,
  0.43280217,
  -0.25493982,
  -0.7743748,
  -1.0317445,
  1.1110668,
  -1.5591248,
  1.9826825,
  -0.24282607,
  -0.41469786,
  -3.3344264,
  0.11363944,
  -2.8590882,
  -1.088034,
  2.4613585,
  -1.1480072,
  -5.038635,
  0.977169,
  2.4759872,
  2.5346713,
  0.3442972,
  1.4619327,
  0.30715242,
  2.9310567,
  -0.59917426,
  0.3880142,
  1.8825564,
  -1.156595,
  -3.876554,
  -3.0197613,
  -3.3022795,
  1.3883591,
  -1.3252974,
  -0.25790408,
  -3.4926305,
  -0.2867509,
  1.2248033,
  1.0775129,
  -0.124073595,
  0.5583523,
  -1.6354872,
  -2.0869143,
  0.9361284,
  0.6112009,
  1.1523937,
  3.9854972,
  0.6371748,
  0.31154326,
  0.5314815,
  -3.1552634,
  0.3829086,
  -1.8355347,
  0.33364198,
  -1.7304109,
  -2.1021266,
  -0.91357166,
  0.5330115,
  -0.42560357,
  -0.56182027,
  2.0372193],
 'jfdi-asia_s': [-1.7572163,
  0.91174996,
  -0.16737428,
  -0.9716258,
  -0.86871153,
  5.658289,
  -1.0651228,
 

In [19]:
node_vocab_size = len(node_params_dict)
node_embedding_size = 64
print(node_vocab_size, node_embedding_size)

682 64


In [20]:
edge_params = []
edge_params_dict = {}
with open(SEA_EDGE_EMBEDDING_FILENAME, "r") as emb_file:
    next(emb_file)
    reader = csv.reader(emb_file, delimiter=" ")
    
    for row in reader:
        node1_name = row[0]
        node2_name = row[1]
#         print(node1_name, node2_name)
        link_name = re.compile(r"(\(')([0-9a-zA-Z_-]+)(\',)").match(node1_name).group(2) + "--" + \
                re.compile(r"(')([0-9a-zA-Z_-]+)(\'\))").match(node2_name).group(2)
        edge_params.append({
            "node1_name": re.compile(r"(\(')([0-9a-zA-Z_-]+)(\',)").match(node1_name).group(2),
            "node2_name": re.compile(r"(')([0-9a-zA-Z_-]+)(\'\))").match(node2_name).group(2),
            "embedding": [float(item) for item in row[2:]]
        })
        edge_params_dict[link_name] = [float(item) for item in row[2:]]
# edge_params
edge_params_dict

{'gocoin--gocoin': [4.775434494018555,
  0.9208109378814697,
  3.089613199234009,
  0.27539345622062683,
  0.17151343822479248,
  0.18731771409511566,
  0.06499431282281876,
  0.5996562838554382,
  1.064496636390686,
  1.2344695329666138,
  2.430870294570923,
  3.931029796600342,
  0.058964502066373825,
  0.171974316239357,
  11.118399620056152,
  0.012913921847939491,
  8.174385070800781,
  1.1838181018829346,
  6.058285713195801,
  1.317920446395874,
  25.387840270996094,
  0.95485919713974,
  6.130512714385986,
  6.424558639526367,
  0.11854056268930435,
  2.137247085571289,
  0.09434261173009872,
  8.591094017028809,
  0.3590098023414612,
  0.15055501461029053,
  3.5440187454223633,
  1.3377119302749634,
  15.027670860290527,
  9.118958473205566,
  10.905049324035645,
  1.927540898323059,
  1.7564131021499634,
  0.0665145143866539,
  12.198467254638672,
  0.08222608268260956,
  1.5001431703567505,
  1.1610339879989624,
  0.015394257381558418,
  0.31175729632377625,
  2.674818277359

In [21]:
edge_vocab_size = len(edge_params_dict)
edge_embedding_size = 64
print(edge_vocab_size, edge_embedding_size)

232903 64


In [22]:
# NOTE: edge embedding seems like will hv a problem in link prediction cos it only takes in the link for 2014
    # 2015 may not have the link, so we don't use it at all?

In [23]:
# using regex
# re.compile(r"\('jfdi-asia_s',").match("('jfdi-asia_s',").group(0)
# re.compile(r"(\(')([a-zA-Z_-]+)(\',)").match("('jfdi-asia_s',").group(2)
# re.compile(r"(')([a-zA-Z_-]+)(\'\))").match("'jfdi-asia_s')").group(2)

In [24]:
pickle.dump( node_params, open( "SEA_node_params.p", "wb" ) )
pickle.dump( node_params_dict, open( "SEA_node_params_dict.p", "wb" ) )
pickle.dump( edge_params, open( "SEA_edge_params.p", "wb" ) )
pickle.dump( edge_params_dict, open( "SEA_edge_params_dict.p", "wb" ) )

In [25]:
node_params = pickle.load( open( "SEA_node_params.p", "rb" ) )
node_params_dict = pickle.load( open( "SEA_node_params_dict.p", "rb" ) )
edge_params = pickle.load( open( "SEA_edge_params.p", "rb" ) )
edge_params_dict = pickle.load( open( "SEA_edge_params_dict.p", "rb" ) )

## Process Embedding Files

In [26]:
SEA_total_records = SEA_data_df_all.shape[0]

# train (0) or test (1)
random.seed(30)
train_index = random.sample(range(SEA_total_records),  int(SEA_total_records*0.7)) #adjust the proportion
test_index = list(set(range(SEA_total_records)) - set(train_index))
print("len(train_index):", len(train_index), ", ", "len(test_index):", len(test_index))

len(train_index): 297116 ,  len(test_index): 127336


In [27]:
# from sklearn import preprocessing
# le = preprocessing.LabelEncoder()
# le.fit(["paris", "paris", "tokyo", "amsterdam"])
# print(list(le.classes_))
# print(le.transform(["tokyo", "tokyo", "paris"]))
# print(list(le.inverse_transform([2, 2, 1])))

In [28]:
# investor side of the bipartite graph
le = LabelEncoder()
le.fit(SEA_data_df_all["from"])
SEA_from_nodes_encoded = le.transform(SEA_data_df_all["from"])
print(SEA_from_nodes_encoded)
print(len(SEA_from_nodes_encoded))
SEA_from_node_name_mapping = dict(zip(le.classes_, le.transform(le.classes_)))
from_node_vocab_size = len(SEA_from_node_name_mapping)
print("\n")
print(from_node_vocab_size)
take(5, SEA_from_node_name_mapping.items())

[  0   0   0 ... 420 420 420]
424452


421


[('500-startups', 0),
 ('8capita-partners', 1),
 ('a-soriano-corporation', 2),
 ('accel-partners', 3),
 ('accel-x-pte-ltd', 4)]

In [29]:
# startup side of the bipartite graph
le = LabelEncoder()
le.fit(SEA_data_df_all["to"])
SEA_to_nodes_encoded = le.transform(SEA_data_df_all["to"])
print(SEA_to_nodes_encoded)
print(len(SEA_to_nodes_encoded))
SEA_to_node_name_mapping = dict(zip(le.classes_, le.transform(le.classes_)))
to_node_vocab_size = len(SEA_to_node_name_mapping)
print("\n")
print(to_node_vocab_size)
take(5, SEA_to_node_name_mapping.items())

[  0 156 102 ... 158 253 197]
424452


261


[('2359-media', 0),
 ('8villages', 1),
 ('99-co', 2),
 ('acommerce_s', 3),
 ('actsocial', 4)]

In [30]:
from_embedding_matrix = np.zeros((from_node_vocab_size, node_embedding_size))

for word, i in SEA_from_node_name_mapping.items():
    from_embedding_vector = node_params_dict.get(word)
    print(i, from_embedding_vector)
    if from_embedding_vector is not None:
        from_embedding_matrix[i] = from_embedding_vector

0 [4.3645616, -1.2592363, -4.418629, -3.3233817, 2.9593616, -2.351, 0.22468863, 1.6911203, 6.005121, -2.1942747, 7.822485, -2.6967342, -0.5995449, -0.54712224, 4.1896133, 5.2112365, -2.0274417, 3.5228708, 2.9845178, 7.5777125, 3.662709, -4.1562195, 2.8635833, 3.48633, -3.04292, -2.7477283, -3.0139782, 0.45802188, -1.850429, 4.069169, -1.8271002, 3.6193755, -2.1098297, -4.183988, -3.5846987, 0.71763575, 3.6638923, -3.0527577, 4.3129416, 1.6520326, -6.16867, -5.010969, -0.36736774, 5.2116117, 2.1206641, 2.694356, -1.185728, -3.2693326, -2.9188814, 5.5729356, 1.4183719, 2.1751199, 2.8153775, -2.1794643, -0.36116585, 4.842713, -2.5086956, 0.53726405, 1.5784817, -1.3173584, -0.62847245, 2.9753485, 2.827452, 0.10471884]
1 [-2.474094, -1.1446544, 3.6021278, 0.40052354, 4.184515, 3.529673, -2.116322, -1.468326, -1.0078311, 5.2052293, -1.4490657, -4.4825416, -2.419115, -1.5367795, -3.297252, 0.94719225, -2.0930429, 0.9648908, -3.1701586, -3.635848, -0.06024998, 0.5400475, 1.0069722, 1.355855, 1

In [31]:
from_embedding_matrix

array([[ 4.3645616e+00, -1.2592363e+00, -4.4186290e+00, ...,
         2.9753485e+00,  2.8274520e+00,  1.0471884e-01],
       [-2.4740940e+00, -1.1446544e+00,  3.6021278e+00, ...,
         2.1789005e+00, -9.8738074e-01, -6.2106717e-01],
       [ 9.1609937e-01,  1.2965468e+00,  1.6587682e+00, ...,
        -1.1641872e+00, -2.8027450e-01, -9.3365810e-01],
       ...,
       [ 1.1582767e+00, -8.4427700e-01, -3.6238965e-01, ...,
         1.2230358e+00, -6.5759850e-02, -4.4315220e-01],
       [-9.2002540e-01, -8.4686294e-02,  2.7763250e+00, ...,
        -1.1870482e-03, -2.6803534e+00, -5.8461535e-01],
       [ 1.4400434e+00,  4.3080652e-01, -1.7340503e+00, ...,
        -2.1626940e+00,  1.1624976e+00, -8.4519210e-01]])

In [32]:
to_embedding_matrix = np.zeros((to_node_vocab_size, node_embedding_size))

for word, i in SEA_to_node_name_mapping.items():
    to_embedding_vector = node_params_dict.get(word)
    print(i, to_embedding_vector)
    if to_embedding_vector is not None:
        to_embedding_matrix[i] = to_embedding_vector

0 [-0.5366473, -0.81347066, -2.4023442, 0.13426206, 1.111222, 0.41612548, 1.6349926, -2.1389017, 1.3008425, -2.0145826, -2.3527656, -1.1436425, 0.84566635, -3.054559, -1.0992086, -3.90492, -3.2428215, 4.280185, 1.5223929, -1.9566388, 0.39728442, 0.7399421, 1.7605861, -1.0282953, 2.9496026, -1.3578064, -3.8700855, 2.2506545, -2.255479, -0.66308105, 0.4874535, 3.689288, 3.7375643, 4.3429103, 2.378789, -3.3135967, -1.7166814, 1.7176012, -0.40170875, 1.3671812, -1.3455924, 0.6243365, -2.4280076, 0.26647314, -1.2390742, -2.3574736, -0.35871994, 2.2973695, 0.40222275, 3.3931293, -0.8757048, -1.389256, -0.27256876, 0.27560678, -2.448475, -1.7413236, -1.6015397, 0.4835901, -0.9911145, 0.46326154, 1.6033384, 0.117874995, -0.2542524, 2.3993614]
1 [0.11431443, -1.216603, -1.4569241, -1.2289491, 0.25340185, 1.5020348, -0.40561238, 2.5190752, 0.73765707, -2.626156, -5.453003, 1.4152889, -3.554581, 2.7209663, -1.6498747, -0.9103113, 2.1433635, -2.3993123, 2.6176505, 1.1041336, -1.0231152, -1.887913,

In [33]:
to_embedding_matrix

array([[-0.5366473 , -0.81347066, -2.4023442 , ...,  0.11787499,
        -0.2542524 ,  2.3993614 ],
       [ 0.11431443, -1.216603  , -1.4569241 , ..., -0.8494026 ,
         2.2161226 , -1.0688182 ],
       [ 3.750322  , -4.7610283 , -4.384793  , ..., -0.45955452,
        -1.3200746 , -5.9268184 ],
       ...,
       [ 2.2620575 , -1.0079554 ,  2.0632265 , ...,  0.11567169,
         0.9862104 , -2.3577676 ],
       [ 0.26672685, -0.47819912,  1.7661915 , ...,  1.3665506 ,
         2.6817117 , -2.5189128 ],
       [-1.2747716 ,  2.20743   ,  0.5653877 , ...,  1.0561781 ,
        -0.6650491 ,  0.3942844 ]])

## Run LSTM Model

In [34]:
first_input = Input(shape=(None,), dtype="int32")
first = Embedding(from_node_vocab_size, node_embedding_size, 
                    weights=[from_embedding_matrix], trainable=False, input_length=1)(first_input)

second_input = Input(shape=(None,), dtype="int32")
second = Embedding(to_node_vocab_size, node_embedding_size, 
                     weights=[to_embedding_matrix], trainable=False, input_length=1)(second_input)

merged = concatenate([first, second])
merged = LSTM(128)(merged)
# merged = Dense(128)(merged)
# merged = Dense(64)(merged)
# merged = Dense(32)(merged)
# merged = Dropout(0.5)(merged)
# merged = Flatten()(merged) #if no LSTM
merged = Dense(1, activation='sigmoid')(merged)

model = Model(inputs=[first_input, second_input], outputs=merged)
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
print(model.summary())

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, None)         0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            (None, None)         0                                            
__________________________________________________________________________________________________
embedding_1 (Embedding)         (None, 1, 64)        26944       input_1[0][0]                    
__________________________________________________________________________________________________
embedding_2 (Embedding)         (None, 1, 64)        16704       input_2[0][0]                    
__________________________________________________________________________________________________
concatenat

In [35]:
start_time = time.time()
# early stopping
es = EarlyStopping(monitor='val_acc', min_delta=0.001, mode='max', verbose=1, patience=2)
# fit the model
model.fit([SEA_from_nodes_encoded[train_index,], SEA_to_nodes_encoded[train_index,]], 
          list(SEA_data_df_all["label"][train_index]), epochs=10, 
          validation_split=0.33, verbose=1, callbacks=[es])
# evaluate the model
loss, accuracy = model.evaluate([SEA_from_nodes_encoded[test_index,], SEA_to_nodes_encoded[test_index,]], 
          list(SEA_data_df_all["label"][test_index]), verbose=1)
print('Accuracy: %f' % accuracy)
print("time taken", time.time() - start_time)

Train on 199067 samples, validate on 98049 samples
Epoch 1/10
199067/199067 [==============================] - 65s 327us/step - loss: 0.0219 - acc: 0.9947 - val_loss: 0.0082 - val_acc: 0.9978
Epoch 2/10
199067/199067 [==============================] - 62s 311us/step - loss: 0.0054 - acc: 0.9984 - val_loss: 0.0047 - val_acc: 0.9984
Epoch 3/10
199067/199067 [==============================] - 62s 311us/step - loss: 0.0026 - acc: 0.9992 - val_loss: 0.0033 - val_acc: 0.9991
Epoch 4/10
199067/199067 [==============================] - 62s 309us/step - loss: 0.0016 - acc: 0.9995 - val_loss: 0.0026 - val_acc: 0.9993
Epoch 5/10
199067/199067 [==============================] - 62s 309us/step - loss: 9.6334e-04 - acc: 0.9997 - val_loss: 0.0020 - val_acc: 0.9996
Epoch 00005: early stopping
127336/127336 [==============================] - 11s 88us/step
Accuracy: 0.999599
time taken 325.03727316856384


In [36]:
y_pred = model.predict([SEA_from_nodes_encoded[test_index,], SEA_to_nodes_encoded[test_index,]], verbose=1)
auroc = roc_auc_score(SEA_data_df_all["label"][test_index], y_pred)
aupr = average_precision_score(SEA_data_df_all["label"][test_index], y_pred)
print("auroc", auroc, "aupr", aupr)

127336/127336 [==============================] - 9s 71us/step
auroc 0.9998752975356427 aupr 0.99732422250826


# CHN

## Create Embedding Files

In [37]:
CHN_NODE_EMBEDDING_FILENAME = "CHN_graph_node.emb"
CHN_EMBEDDING_MODEL_FILENAME = "CHN_graph_model.model"
CHN_EDGE_EMBEDDING_FILENAME= "CHN_graph_edge.emb"

In [38]:
# Precompute probabilities and generate walks - **ON WINDOWS ONLY WORKS WITH workers=1**
node2vec = Node2Vec(CHN_data_graph, dimensions=64, walk_length=30, num_walks=200, workers=4)  # Use temp_folder for big graphs

# Embed nodes
model = node2vec.fit(window=10, min_count=1, batch_words=4)  # Any keywords acceptable by gensim.Word2Vec can be passed, `diemnsions` and `workers` are automatically passed (from the Node2Vec constructor)

# Save embeddings for later use
model.wv.save_word2vec_format(CHN_NODE_EMBEDDING_FILENAME)

# Save model for later use|
model.save(CHN_EMBEDDING_MODEL_FILENAME)

edges_embs = HadamardEmbedder(keyed_vectors=model.wv)

Computing transition probabilities: 100%|██████████| 1143/1143 [00:00<00:00, 6808.06it/s]


In [39]:
# Get all edges in a separate KeyedVectors instance - use with caution could be huge for big networks
edges_kv = edges_embs.as_keyed_vectors()

# Save embeddings for later use
edges_kv.save_word2vec_format(CHN_EDGE_EMBEDDING_FILENAME)

Generating edge features: 100%|██████████| 653796/653796.0 [00:03<00:00, 172882.70it/s]


## Reading in Embedding Files

In [40]:
node_params = []
node_params_dict = {}
with open(CHN_NODE_EMBEDDING_FILENAME, "r") as emb_file:
    next(emb_file)
    reader = csv.reader(emb_file, delimiter=" ")
    for row in reader:
        node_name = row[0]
        node_params.append({
            "name": node_name,
            "embedding": [float(item) for item in row[1:]]
        })
        node_params_dict[node_name] = [float(item) for item in row[1:]]
# node_params
node_params_dict

{'sequoia-capital': [2.566006,
  -1.558212,
  5.8664613,
  -3.9494328,
  -1.7885636,
  1.2728986,
  -0.24733381,
  0.9968886,
  3.0951037,
  -2.9044864,
  1.9541246,
  -1.9002901,
  2.0256095,
  3.1894138,
  -1.3057073,
  -5.8348975,
  -1.2441087,
  7.3287177,
  4.2870293,
  -1.9887927,
  0.82137567,
  -1.3843211,
  7.6114597,
  1.0272573,
  -0.77224845,
  1.8061882,
  3.4685588,
  2.2836108,
  0.7135765,
  -2.7307491,
  3.0432618,
  -0.34352118,
  1.8918144,
  3.4389362,
  3.8244538,
  0.46394777,
  -0.2347526,
  1.6143563,
  -6.8389053,
  2.6492903,
  0.26897937,
  -3.2287273,
  -0.0025326842,
  0.9608553,
  6.779738,
  -5.5357594,
  -1.2894634,
  3.4050484,
  -3.756346,
  3.8046286,
  3.4300613,
  -0.7952407,
  4.327112,
  0.047195256,
  -2.2822354,
  -0.48509774,
  -3.9164963,
  5.7335114,
  -4.158693,
  -3.2783163,
  -3.3048658,
  -0.85188746,
  -1.7834176,
  -4.1163774],
 'cyberport-hong-kong': [4.7514024,
  -3.791132,
  0.10386465,
  0.5135493,
  0.5156073,
  -3.3297577,
  1.271

In [41]:
node_vocab_size = len(node_params_dict)
node_embedding_size = 64
print(node_vocab_size, node_embedding_size)

1143 64


In [42]:
edge_params = []
edge_params_dict = {}
with open(CHN_EDGE_EMBEDDING_FILENAME, "r") as emb_file:
    next(emb_file)
    reader = csv.reader(emb_file, delimiter=" ")
    
    for row in reader:
        node1_name = row[0]
        node2_name = row[1]
#         print(node1_name, node2_name)
        link_name = re.compile(r"(\(')([0-9a-zA-Z_-]+)(\',)").match(node1_name).group(2) + "--" + \
                re.compile(r"(')([0-9a-zA-Z_-]+)(\'\))").match(node2_name).group(2)
        edge_params.append({
            "node1_name": re.compile(r"(\(')([0-9a-zA-Z_-]+)(\',)").match(node1_name).group(2),
            "node2_name": re.compile(r"(')([0-9a-zA-Z_-]+)(\'\))").match(node2_name).group(2),
            "embedding": [float(item) for item in row[2:]]
        })
        edge_params_dict[link_name] = [float(item) for item in row[2:]]
# edge_params
edge_params_dict

{'sequoia-capital--sequoia-capital': [6.584386348724365,
  2.4280247688293457,
  34.415367126464844,
  15.59801959991455,
  3.1989598274230957,
  1.6202707290649414,
  0.06117401272058487,
  0.9937868118286133,
  9.579667091369629,
  8.436040878295898,
  3.8186028003692627,
  3.61110258102417,
  4.10309362411499,
  10.17236042022705,
  1.704871654510498,
  34.04602813720703,
  1.5478063821792603,
  53.71010208129883,
  18.378620147705078,
  3.955296277999878,
  0.6746580004692078,
  1.9163448810577393,
  57.93431854248047,
  1.0552575588226318,
  0.5963676571846008,
  3.2623159885406494,
  12.030900001525879,
  5.214878559112549,
  0.5091913938522339,
  7.456990718841553,
  9.261442184448242,
  0.11800680309534073,
  3.5789616107940674,
  11.826282501220703,
  14.626446723937988,
  0.21524754166603088,
  0.05510878190398216,
  2.6061460971832275,
  46.770626068115234,
  7.018739223480225,
  0.0723498985171318,
  10.424680709838867,
  6.414489689632319e-06,
  0.9232429265975952,
  45.96

In [43]:
edge_vocab_size = len(edge_params_dict)
edge_embedding_size = 64
print(edge_vocab_size, edge_embedding_size)

653796 64


In [44]:
# NOTE: edge embedding seems like will hv a problem in link prediction cos it only takes in the link for 2014
    # 2015 may not have the link, so we don't use it at all?

In [45]:
# using regex
# re.compile(r"\('jfdi-asia_s',").match("('jfdi-asia_s',").group(0)
# re.compile(r"(\(')([a-zA-Z_-]+)(\',)").match("('jfdi-asia_s',").group(2)
# re.compile(r"(')([a-zA-Z_-]+)(\'\))").match("'jfdi-asia_s')").group(2)

In [46]:
pickle.dump( node_params, open( "CHN_node_params.p", "wb" ) )
pickle.dump( node_params_dict, open( "CHN_node_params_dict.p", "wb" ) )
pickle.dump( edge_params, open( "CHN_edge_params.p", "wb" ) )
pickle.dump( edge_params_dict, open( "CHN_edge_params_dict.p", "wb" ) )

In [47]:
node_params = pickle.load( open( "CHN_node_params.p", "rb" ) )
node_params_dict = pickle.load( open( "CHN_node_params_dict.p", "rb" ) )
edge_params = pickle.load( open( "CHN_edge_params.p", "rb" ) )
edge_params_dict = pickle.load( open( "CHN_edge_params_dict.p", "rb" ) )

## Process Embedding Files

In [48]:
CHN_total_records = CHN_data_df_all.shape[0]

# train (0) or test (1)
random.seed(30)
train_index = random.sample(range(CHN_total_records),  int(CHN_total_records*0.7)) #adjust the proportion
test_index = list(set(range(CHN_total_records)) - set(train_index))
print("len(train_index):", len(train_index), ", ", "len(test_index):", len(test_index))

len(train_index): 1289964 ,  len(test_index): 552842


In [49]:
# from sklearn import preprocessing
# le = preprocessing.LabelEncoder()
# le.fit(["paris", "paris", "tokyo", "amsterdam"])
# print(list(le.classes_))
# print(le.transform(["tokyo", "tokyo", "paris"]))
# print(list(le.inverse_transform([2, 2, 1])))

In [50]:
# investor side of the bipartite graph
le = LabelEncoder()
le.fit(CHN_data_df_all["from"])
CHN_from_nodes_encoded = le.transform(CHN_data_df_all["from"])
print(CHN_from_nodes_encoded)
print(len(CHN_from_nodes_encoded))
CHN_from_node_name_mapping = dict(zip(le.classes_, le.transform(le.classes_)))
from_node_vocab_size = len(CHN_from_node_name_mapping)
print("\n")
print(from_node_vocab_size)
take(5, CHN_from_node_name_mapping.items())

[  0   0   0 ... 450 450 450]
1842806


451


[('36kr_i', 0),
 ('500-startups', 1),
 ('abrt', 2),
 ('acceleratorhk', 3),
 ('adam-bornstein', 4)]

In [51]:
# startup side of the bipartite graph
le = LabelEncoder()
le.fit(CHN_data_df_all["to"])
CHN_to_nodes_encoded = le.transform(CHN_data_df_all["to"])
print(CHN_to_nodes_encoded)
print(len(CHN_to_nodes_encoded))
CHN_to_node_name_mapping = dict(zip(le.classes_, le.transform(le.classes_)))
to_node_vocab_size = len(CHN_to_node_name_mapping)
print("\n")
print(to_node_vocab_size)
take(5, CHN_to_node_name_mapping.items())

[513 308  14 ... 619 288 380]
1842806


692


[('01games-technology', 0),
 ('1006-tv', 1),
 ('117go', 2),
 ('17u-cn', 3),
 ('19pay', 4)]

In [52]:
from_embedding_matrix = np.zeros((from_node_vocab_size, node_embedding_size))

for word, i in CHN_from_node_name_mapping.items():
    from_embedding_vector = node_params_dict.get(word)
    print(i, from_embedding_vector)
    if from_embedding_vector is not None:
        from_embedding_matrix[i] = from_embedding_vector

0 [-1.6237966, 1.369826, -2.6853025, 1.2311095, -0.89249086, -2.2032285, 3.8534124, 1.1094006, 0.09924428, 0.81924736, -1.0984523, 1.3078225, -0.989857, -0.8591283, -0.6856292, -0.9217942, 1.106159, 0.8436419, -0.40676016, -0.4270822, 0.117280446, 2.3729038, -1.8388776, 2.3599005, 3.941164, -0.15492694, -1.775215, -2.5979512, 1.0001017, -2.3250327, -0.93189394, -0.87306505, 1.129738, -1.6641499, 0.018919209, -3.3302274, 1.6269286, 2.6659062, 4.014205, 0.69356024, 1.142568, 1.421008, 1.0202447, 2.1482825, -3.8588018, -2.4447532, -3.1524937, 1.3802795, 1.5794787, 0.8406995, -3.1880336, 1.5386252, -0.79785156, 3.8384562, 1.9284439, 2.3350468, -1.1762344, 3.8610556, 1.7657428, -1.2976863, -0.8827256, 4.1255646, 4.773008, -4.8173437]
1 [-3.822891, -3.811407, 4.654496, 6.871922, 2.4033706, 1.7124145, 2.7733943, 5.1226463, 0.95917594, -2.4735928, 2.5925343, -5.158394, 2.8086896, -2.5093899, -0.77476, -2.1367834, -0.8061507, -4.611636, -6.9708347, 3.3012457, 0.3962496, 0.9056559, 5.3672285, -3

In [53]:
from_embedding_matrix

array([[-1.6237966 ,  1.369826  , -2.6853025 , ...,  4.1255646 ,
         4.773008  , -4.8173437 ],
       [-3.822891  , -3.811407  ,  4.654496  , ..., -0.3972326 ,
         0.4528793 ,  4.967847  ],
       [-1.1680119 ,  1.1325413 , -0.01185178, ...,  1.3469595 ,
        -0.5390152 , -1.1779873 ],
       ...,
       [-0.2431893 , -4.9970927 ,  4.6858068 , ...,  1.2307979 ,
        -3.2132454 , -2.0221417 ],
       [-2.036207  , -0.84438264,  2.258494  , ..., -4.6731815 ,
         2.2548897 , -0.80781   ],
       [-1.8758633 , -1.1059506 , -0.74563825, ...,  0.18881325,
         0.4078779 , -0.40118122]])

In [54]:
to_embedding_matrix = np.zeros((to_node_vocab_size, node_embedding_size))

for word, i in CHN_to_node_name_mapping.items():
    to_embedding_vector = node_params_dict.get(word)
    print(i, to_embedding_vector)
    if to_embedding_vector is not None:
        to_embedding_matrix[i] = to_embedding_vector

0 [0.25604486, 0.12683211, -2.0107903, 1.0297995, 0.40871608, -1.2945323, 1.677073, 0.42414832, -0.20567025, 0.21812625, -0.54793406, -1.508259, -1.4046725, -1.4886112, -0.41852835, 1.0225624, -2.3377934, -0.831671, -0.6648217, -1.8136176, -0.4900892, 1.5791689, 1.7965589, 1.883058, -0.4441541, -0.99804443, -0.63236356, -0.7813639, -0.13812873, -0.9627984, -0.8405653, -1.73538, -2.3272772, -1.4983357, 2.6240168, -0.7108006, -0.82929015, -0.27776212, 3.9328647, -0.15383865, 1.1473145, 0.21927132, -0.3516937, -0.2712337, -0.1539411, 1.522304, 0.5895495, -0.5596984, 3.394917, 2.1470544, -1.51612, 0.90179056, -1.0638374, -0.92615724, 0.6780468, -1.4806262, -0.31358838, 0.56839854, 3.1929998, 0.027212324, -0.6740429, 2.378347, -0.4631198, 2.686294]
1 [-2.064813, 1.8930199, 2.5832386, -2.2598605, -3.7499945, 1.3259803, 0.2273248, 1.9473803, 5.0104465, -1.3526416, 3.5243945, -0.88787144, -0.63568884, -0.45574048, 5.0106235, -2.2085793, -0.49165067, 0.46341246, 1.3516276, -2.345864, -2.5077164

263 [-2.4555516, 0.5933218, -2.7071955, 2.5209286, -3.2282917, -1.156837, -1.7138249, -0.10440993, -1.938883, -1.6599144, 3.4627604, 0.011569258, -0.9362818, 1.4664028, -2.0507786, -1.8283503, 0.38151032, 2.0761461, -0.24315262, -2.0407455, 2.6328135, 0.96534574, -1.2220476, -2.5680254, 2.5196002, -0.2632427, 0.53431517, 2.4426677, 0.6633843, -1.723197, 0.8543812, -2.9256067, 1.3380824, 4.184195, -1.7560427, 0.35946393, 1.7584281, -2.1233177, 3.8158555, 0.30816343, -4.14349, 5.7745347, 2.7330842, 1.9557867, 2.778346, -0.44552675, -3.1851442, 1.4871371, -0.9528643, 1.0271568, 0.5160149, 0.03511659, -1.363816, -0.35064104, -2.0570774, -0.5038639, -1.5511532, -2.5197492, 1.9803933, 0.57476354, -0.6730704, -0.32896385, -0.5533598, -0.6401498]
264 [0.5370417, 2.374318, 3.6307952, -3.8380303, 3.6418765, 3.1808503, 1.9614389, 2.3978505, 1.4925138, -0.5131488, 5.575707, -9.268186, 2.989557, 6.6167636, 3.3421254, -0.97670335, 0.7705762, -2.4235914, 4.0492125, -0.91585153, -1.1329855, -0.7372692

414 [0.29489225, 3.725962, 7.1175675, -3.537739, -4.666835, -2.7378533, 1.5598623, 2.4526908, -1.3853656, -4.146851, 7.546669, 0.77066714, 4.6345778, 5.8061256, -0.22013435, 3.1079504, -1.957677, 1.3354937, 2.1592057, -2.1623273, 1.8584648, 4.2555423, 3.7427156, 1.7244171, -4.1756496, 2.0261528, 0.24956588, -3.109248, 2.3085563, -0.46479797, 2.5985873, 0.98444045, 1.392622, 0.6884831, 6.679434, 0.6241764, 5.6855855, 5.1815114, -3.195364, 5.2102213, -3.1974318, -7.415668, -2.2752826, -4.047854, 0.030787246, -5.774264, -1.8674203, -0.026198223, -5.798058, -0.30246425, -5.8124676, -0.1262107, -1.3569169, -0.04253141, -7.233803, -3.3813152, 1.8040664, 1.3736291, 1.4927585, -2.1507375, -0.35290274, -2.8481283, -1.013453, -4.528916]
415 [-2.6453402, -0.8654717, -5.0569615, 1.934554, 1.457424, -2.6369934, 0.4406727, -0.6582837, 3.6225643, 3.8349059, 6.119585, 1.4430335, 3.999209, -2.04308, 1.3482983, 1.9586775, 0.31922475, 1.1884714, -0.08836416, 3.3999434, -1.1737317, -2.0296845, 3.9513853, 

564 [0.99970436, 0.02301575, 3.3761158, -2.1183083, 0.08774106, 0.8324125, -0.108341105, 1.7302419, 3.6801262, -1.5396408, 2.3453426, -1.8640848, -0.2767735, 0.15854353, -0.8499203, -1.5396861, -0.7431263, 1.7552589, 0.37977284, -1.2369221, -0.8018404, -0.38099158, 4.0845447, 1.4000423, -0.25330856, 2.1077266, 2.8386095, -0.22254114, 1.5018808, -1.3523401, 1.285035, -0.5721794, -1.3725752, 1.7399595, 0.7959673, 0.49727923, 0.47731724, 3.6556714, -2.2904, 2.889189, 0.35218775, -1.6933906, 0.3464981, -1.3094814, 3.2172334, -4.1771812, -1.7187694, -0.17311019, -1.6654269, 2.977431, 0.6232152, 1.493886, 1.3835082, 1.1178992, -0.6970987, -1.7513642, -1.3902487, 1.0960183, 0.004900208, -0.76951873, -0.09174346, 1.5834863, -0.9336303, -2.684237]
565 [0.401809, 0.13966836, -1.7855672, 0.979187, 0.6866606, -1.1860822, 1.8030937, 0.4098918, 0.08732778, 0.4909412, -0.2320896, -1.1962074, -1.072377, -1.1535044, -0.24663126, 1.0579085, -2.494851, -0.94014287, -0.56717, -1.9823546, -0.99168694, 1.22

In [55]:
to_embedding_matrix

array([[ 0.25604486,  0.12683211, -2.0107903 , ...,  2.378347  ,
        -0.4631198 ,  2.686294  ],
       [-2.064813  ,  1.8930199 ,  2.5832386 , ...,  0.77299976,
        -0.9057637 , -1.3274328 ],
       [-1.0743942 , -1.1552446 , -0.04319871, ...,  2.1792529 ,
         1.752299  , -2.4373066 ],
       ...,
       [-0.10166049,  2.1538095 ,  0.41323134, ...,  1.6615323 ,
         1.3663534 , -0.18390064],
       [-1.8852943 , -0.9697734 ,  0.6314865 , ...,  0.58564967,
         1.2749456 , -3.204972  ],
       [-0.4471926 ,  0.24300481, -2.9653661 , ...,  1.600592  ,
        -2.124888  , -2.3238564 ]])

## Run LSTM Model

In [56]:
first_input = Input(shape=(None,), dtype="int32")
first = Embedding(from_node_vocab_size, node_embedding_size, 
                    weights=[from_embedding_matrix], trainable=False, input_length=1)(first_input)

second_input = Input(shape=(None,), dtype="int32")
second = Embedding(to_node_vocab_size, node_embedding_size, 
                     weights=[to_embedding_matrix], trainable=False, input_length=1)(second_input)

merged = concatenate([first, second])
merged = LSTM(128)(merged)
# merged = Dense(128)(merged)
# merged = Dense(64)(merged)
# merged = Dense(32)(merged)
# merged = Dropout(0.5)(merged)
# merged = Flatten()(merged) # if no LSTM
merged = Dense(1, activation='sigmoid')(merged)

model = Model(inputs=[first_input, second_input], outputs=merged)
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
print(model.summary())

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_3 (InputLayer)            (None, None)         0                                            
__________________________________________________________________________________________________
input_4 (InputLayer)            (None, None)         0                                            
__________________________________________________________________________________________________
embedding_3 (Embedding)         (None, 1, 64)        28864       input_3[0][0]                    
__________________________________________________________________________________________________
embedding_4 (Embedding)         (None, 1, 64)        44288       input_4[0][0]                    
__________________________________________________________________________________________________
concatenat

In [57]:
start_time = time.time()
# early stopping
es = EarlyStopping(monitor='val_acc', min_delta=0.001, mode='max', verbose=1, patience=2)
# fit the model
model.fit([CHN_from_nodes_encoded[train_index,], CHN_to_nodes_encoded[train_index,]], 
          list(CHN_data_df_all["label"][train_index]), epochs=10, 
          validation_split=0.33, verbose=1, callbacks=[es])
# evaluate the model
loss, accuracy = model.evaluate([CHN_from_nodes_encoded[test_index,], CHN_to_nodes_encoded[test_index,]], 
          list(CHN_data_df_all["label"][test_index]), verbose=1)
print('Accuracy: %f' % accuracy)
print("time taken", time.time() - start_time)

Train on 864275 samples, validate on 425689 samples
Epoch 1/10
864275/864275 [==============================] - 273s 316us/step - loss: 0.0089 - acc: 0.9977 - val_loss: 0.0026 - val_acc: 0.9993
Epoch 2/10
864275/864275 [==============================] - 272s 314us/step - loss: 0.0019 - acc: 0.9995 - val_loss: 0.0017 - val_acc: 0.9996
Epoch 3/10
864275/864275 [==============================] - 272s 314us/step - loss: 9.9246e-04 - acc: 0.9997 - val_loss: 0.0011 - val_acc: 0.9997
Epoch 00003: early stopping
552842/552842 [==============================] - 49s 90us/step
Accuracy: 0.999738
time taken 872.6256628036499


In [58]:
y_pred = model.predict([CHN_from_nodes_encoded[test_index,], CHN_to_nodes_encoded[test_index,]], verbose=1)
auroc = roc_auc_score(CHN_data_df_all["label"][test_index], y_pred)
aupr = average_precision_score(CHN_data_df_all["label"][test_index], y_pred)
print("auroc", auroc, "aupr", aupr)

552842/552842 [==============================] - 40s 73us/step
auroc 0.9999683212132081 aupr 0.9995002145311337
